In [1]:
import pandas as pd
import numpy as np
import scipy as sp
import scipy.stats as stats
import matplotlib as mpl
import matplotlib.pyplot as plt
import statistics
import csv
import pickle 
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import RandomizedSearchCV
from sklearn.metrics import roc_auc_score
from sklearn.metrics import f1_score
from sklearn.metrics import log_loss
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import RobustScaler
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import LabelEncoder

In [2]:
#get whole transcriptome df
with open('LNglyconorm_split.pkl', 'rb') as f:
   dict_for_model = pickle.load(f)

#get whole transcriptome ranked feature list
with open('fullLNfeats_2.pkl', 'rb') as f:
   fullgenelist = pickle.load(f)

#get list of RANKED glycogenes, no housekeeping (should be 216 long)
with open('glycoLNfeats_2.pkl', 'rb') as f:
   ranked_glycogenes = pickle.load(f)

#make list of ranked glycogenes from imported df
ranked_glycogenes = ranked_glycogenes['feature'].values.tolist()

In [12]:
'''
Model evaluation
'''

def model_evaluation(model, x, y):
    
    model_predict = model.predict(x)
    model_predict_prob = model.predict_proba(x)
    
    high = f"{100*(model.score(x[y==1], y[y==1])):>4f}%"
    low = f'{100*(model.score(x[y==0], y[y==0])):>4f}%'
    total = f'{100*(model.score(x, y)):>4f}%'

    avg_loss = log_loss(y, model_predict_prob)
    roc_auc = roc_auc_score(y, model_predict)
    f1 = f1_score(y, model_predict)
    return high, low, total, avg_loss, roc_auc, f1

In [13]:
'''
Generate training, validation, and test set from original full df using scikit learn 
saves best estimator model as a pickle

Input: 
- dataframe with PHA-L column (binary) and transcripts

Output: 
- high, low, total accuracy of best estimator model 
'''
def train_and_evaluate(data, random_number):
    #y: PHA-L score array
    y = data['PHA-L'].values 

    #X: glycogene transcript data array
    x = data.iloc[:, 3:].values   

    # Split training, validation and test set
    x_train, x_test, y_train, y_test = train_test_split(
        x, y, test_size=0.1, random_state=random_number, stratify=y)

    encoder = LabelEncoder()
    y_train = encoder.fit_transform(y_train)
    y_test = encoder.fit_transform(y_test)
    
    ''''Use RandomSearchCV to optimize hyperparameters'''
    #takes a while to run!!
    model = RandomForestClassifier()

    model_random = RandomizedSearchCV(estimator = model, param_distributions = random_grid, 
                                      n_iter = 20, cv = 5, verbose=5, random_state=random_number, n_jobs = -1)

    model_random.fit(x_train, y_train)
    
    mod = model_random.best_estimator_
    
    high, low, total, avg_loss, roc_auc, f1 = model_evaluation(mod, x_test, y_test)
    
    return high, low, total, avg_loss, roc_auc, f1



In [15]:

'''
Adding glycogenes 1 by one to model 
'''

#auROC for 3 full glycogene models
whole_glycogene_AUC_arr = [0.785557, 0.787447, 0.786859] #change depending on model

# Parameters for grid search
# Number of trees in random forest
n_estimators = [int(x) for x in np.arange(200, 800, step=100)]
# Maximum number of levels in tree
max_depth = [int(x) for x in np.arange(10, 50, step=10)]
max_depth.append(None)
# Minimum number of samples required to split a node
min_samples_split = [2, 5]
# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2]
# Create the random grid
random_grid = {'n_estimators': n_estimators,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf,
               }



counter = 1

tag_list = ['Biotin', 'Type', 'PHA-L']
base_list = tag_list + [ranked_glycogenes[0]]

extra_glycogenes = ranked_glycogenes[1:]

cols_to_add = [] #starts empty, populates with 5 genes each iteration of the while loop

all_cols_for_df = base_list #initialize columnn selection for first df

#make df of evaluation of models
master_df = pd.DataFrame(columns=['row_name', 'input', 'high', 'low', 'total', 'avg_loss', 'roc_auc', 'f1', 'genes']) #initialize df to compile results

#make df to store p vals to compare each model to whole glycogene model
pval_df = pd.DataFrame(columns=['count', 'statistic', 'pval', 'genes'])


while True: 
    for key, df in dict_for_model.items():
        high, low, total, avg_loss, roc_auc, f1 = train_and_evaluate(df[all_cols_for_df], 42) 

        new_row = {'row_name': f"results{counter}_{key}",
                                        'input': key, 'high': high, 'low': low,
                                        'total': total,'avg_loss': avg_loss, 'roc_auc': roc_auc, 'f1': f1, 
                                        'genes': all_cols_for_df }
        master_df.loc[len(master_df)] = new_row
    temp_array = master_df['roc_auc'].tail(3) #get array of the three roc_auc results from most recent evaluation
    statistic, p_value = stats.ttest_rel(whole_glycogene_AUC_arr, temp_array) #get p val 
    print(counter) #see how code is progressing while running
    n_row = {'count': counter, 'statistic': statistic, 'pval': p_value, 'genes': all_cols_for_df}
    pval_df.loc[len(pval_df)] = n_row
    print('length of genes left:')
    print(len(extra_glycogenes))
          
    #break if run out of extra genes to add
    if len(extra_glycogenes) == 0:
        break
    if len(extra_glycogenes) != 0:
        cols_to_add.extend(extra_glycogenes[:1])
        extra_glycogenes = extra_glycogenes[1:]
        all_cols_for_df = base_list + cols_to_add
        counter += 1
    else:
        break
          
#save dfs
with open('master_df_glycogene_countdown_LN_split_df.pkl', 'wb') as f:
    pickle.dump(master_df, f)
          
with open('master_df_glycogene_countdown_LN_split_pval.pkl', 'wb') as f:
    pickle.dump(pval_df, f)

Fitting 5 folds for each of 20 candidates, totalling 100 fits
Fitting 5 folds for each of 20 candidates, totalling 100 fits
Fitting 5 folds for each of 20 candidates, totalling 100 fits
1
length of genes left:
214
Fitting 5 folds for each of 20 candidates, totalling 100 fits
Fitting 5 folds for each of 20 candidates, totalling 100 fits
Fitting 5 folds for each of 20 candidates, totalling 100 fits
2
length of genes left:
213
Fitting 5 folds for each of 20 candidates, totalling 100 fits
Fitting 5 folds for each of 20 candidates, totalling 100 fits
Fitting 5 folds for each of 20 candidates, totalling 100 fits
3
length of genes left:
212
Fitting 5 folds for each of 20 candidates, totalling 100 fits
Fitting 5 folds for each of 20 candidates, totalling 100 fits
Fitting 5 folds for each of 20 candidates, totalling 100 fits
4
length of genes left:
211
Fitting 5 folds for each of 20 candidates, totalling 100 fits
Fitting 5 folds for each of 20 candidates, totalling 100 fits
[CV 3/5] END max_dep

Fitting 5 folds for each of 20 candidates, totalling 100 fits
[CV 1/5] END max_depth=20, min_samples_leaf=2, min_samples_split=5, n_estimators=400;, score=0.683 total time=   1.2s
[CV 4/5] END max_depth=30, min_samples_leaf=2, min_samples_split=2, n_estimators=600;, score=0.656 total time=   1.8s
[CV 1/5] END max_depth=30, min_samples_leaf=2, min_samples_split=2, n_estimators=400;, score=0.683 total time=   1.2s
[CV 3/5] END max_depth=40, min_samples_leaf=2, min_samples_split=2, n_estimators=700;, score=0.647 total time=   1.8s
[CV 3/5] END max_depth=20, min_samples_leaf=2, min_samples_split=5, n_estimators=700;, score=0.647 total time=   2.1s
[CV 4/5] END max_depth=20, min_samples_leaf=2, min_samples_split=2, n_estimators=600;, score=0.656 total time=   1.8s
[CV 4/5] END max_depth=20, min_samples_leaf=2, min_samples_split=2, n_estimators=200;, score=0.656 total time=   0.6s
[CV 4/5] END max_depth=None, min_samples_leaf=2, min_samples_split=2, n_estimators=300;, score=0.656 total time=

[CV 5/5] END max_depth=10, min_samples_leaf=1, min_samples_split=2, n_estimators=600;, score=0.671 total time=   1.8s
[CV 2/5] END max_depth=10, min_samples_leaf=1, min_samples_split=5, n_estimators=600;, score=0.670 total time=   1.8s
[CV 4/5] END max_depth=10, min_samples_leaf=1, min_samples_split=5, n_estimators=700;, score=0.656 total time=   2.1s
[CV 5/5] END max_depth=20, min_samples_leaf=2, min_samples_split=5, n_estimators=400;, score=0.684 total time=   1.2s
[CV 2/5] END max_depth=40, min_samples_leaf=1, min_samples_split=2, n_estimators=300;, score=0.670 total time=   0.9s
[CV 2/5] END max_depth=20, min_samples_leaf=2, min_samples_split=2, n_estimators=600;, score=0.670 total time=   1.8s
[CV 5/5] END max_depth=20, min_samples_leaf=2, min_samples_split=2, n_estimators=200;, score=0.684 total time=   0.6s
[CV 5/5] END max_depth=None, min_samples_leaf=2, min_samples_split=2, n_estimators=300;, score=0.684 total time=   0.9s
[CV 4/5] END max_depth=None, min_samples_leaf=1, min_s

[CV 1/5] END max_depth=20, min_samples_leaf=1, min_samples_split=2, n_estimators=400;, score=0.683 total time=   1.2s
[CV 3/5] END max_depth=40, min_samples_leaf=1, min_samples_split=2, n_estimators=300;, score=0.647 total time=   0.9s
[CV 5/5] END max_depth=None, min_samples_leaf=1, min_samples_split=5, n_estimators=700;, score=0.684 total time=   2.1s
[CV 4/5] END max_depth=None, min_samples_leaf=2, min_samples_split=2, n_estimators=300;, score=0.656 total time=   0.9s
[CV 4/5] END max_depth=None, min_samples_leaf=1, min_samples_split=5, n_estimators=400;, score=0.656 total time=   0.9s
[CV 4/5] END max_depth=10, min_samples_leaf=1, min_samples_split=2, n_estimators=600;, score=0.656 total time=   1.8s
[CV 4/5] END max_depth=10, min_samples_leaf=1, min_samples_split=5, n_estimators=600;, score=0.656 total time=   1.8s
[CV 1/5] END max_depth=20, min_samples_leaf=2, min_samples_split=2, n_estimators=200;, score=0.683 total time=   0.6s
[CV 5/5] END max_depth=40, min_samples_leaf=2, min

[CV 2/5] END max_depth=30, min_samples_leaf=1, min_samples_split=5, n_estimators=300;, score=0.670 total time=   0.9s
[CV 4/5] END max_depth=20, min_samples_leaf=1, min_samples_split=2, n_estimators=400;, score=0.656 total time=   1.2s
[CV 3/5] END max_depth=None, min_samples_leaf=1, min_samples_split=5, n_estimators=700;, score=0.647 total time=   2.0s
[CV 1/5] END max_depth=40, min_samples_leaf=2, min_samples_split=5, n_estimators=300;, score=0.683 total time=   0.9s
[CV 3/5] END max_depth=10, min_samples_leaf=1, min_samples_split=2, n_estimators=200;, score=0.647 total time=   0.6s
[CV 3/5] END max_depth=20, min_samples_leaf=2, min_samples_split=5, n_estimators=400;, score=0.647 total time=   1.2s
[CV 5/5] END max_depth=30, min_samples_leaf=2, min_samples_split=2, n_estimators=600;, score=0.684 total time=   1.8s
[CV 3/5] END max_depth=30, min_samples_leaf=2, min_samples_split=2, n_estimators=400;, score=0.647 total time=   1.2s
[CV 4/5] END max_depth=40, min_samples_leaf=2, min_sam

...

[CV 3/5] END max_depth=10, min_samples_leaf=1, min_samples_split=2, n_estimators=200;, score=0.768 total time=   0.7s
[CV 1/5] END max_depth=20, min_samples_leaf=2, min_samples_split=5, n_estimators=700;, score=0.780 total time=   3.0s
[CV 3/5] END max_depth=30, min_samples_leaf=2, min_samples_split=2, n_estimators=600;, score=0.776 total time=   2.7s
[CV 1/5] END max_depth=10, min_samples_leaf=2, min_samples_split=5, n_estimators=200;, score=0.794 total time=   0.8s
[CV 5/5] END max_depth=10, min_samples_leaf=1, min_samples_split=5, n_estimators=700;, score=0.753 total time=   2.5s
[CV 2/5] END max_depth=40, min_samples_leaf=2, min_samples_split=2, n_estimators=600;, score=0.760 total time=   2.6s
[CV 4/5] END max_depth=10, min_samples_leaf=1, min_samples_split=2, n_estimators=600;, score=0.826 total time=   2.2s
[CV 5/5] END max_depth=40, min_samples_leaf=1, min_samples_split=2, n_estimators=300;, score=0.781 total time=   1.6s
[CV 1/5] END max_depth=30, min_samples_leaf=2, min_sampl

[CV 4/5] END max_depth=None, min_samples_leaf=2, min_samples_split=2, n_estimators=300;, score=0.840 total time=   1.6s
[CV 2/5] END max_depth=20, min_samples_leaf=2, min_samples_split=5, n_estimators=700;, score=0.749 total time=   2.9s
[CV 5/5] END max_depth=30, min_samples_leaf=2, min_samples_split=2, n_estimators=600;, score=0.752 total time=   3.1s
[CV 2/5] END max_depth=30, min_samples_leaf=2, min_samples_split=2, n_estimators=400;, score=0.763 total time=   1.8s
[CV 5/5] END max_depth=40, min_samples_leaf=2, min_samples_split=2, n_estimators=700;, score=0.756 total time=   3.7s
[CV 2/5] END max_depth=10, min_samples_leaf=1, min_samples_split=2, n_estimators=600;, score=0.755 total time=   2.4s
[CV 1/5] END max_depth=40, min_samples_leaf=1, min_samples_split=2, n_estimators=300;, score=0.777 total time=   2.0s
[CV 1/5] END max_depth=10, min_samples_leaf=2, min_samples_split=5, n_estimators=200;, score=0.790 total time=   1.1s
[CV 5/5] END max_depth=10, min_samples_leaf=1, min_sam

[CV 2/5] END max_depth=40, min_samples_leaf=2, min_samples_split=2, n_estimators=700;, score=0.761 total time=   3.2s
[CV 4/5] END max_depth=None, min_samples_leaf=1, min_samples_split=5, n_estimators=400;, score=0.790 total time=   2.0s
[CV 1/5] END max_depth=20, min_samples_leaf=1, min_samples_split=2, n_estimators=400;, score=0.794 total time=   1.9s
[CV 3/5] END max_depth=20, min_samples_leaf=2, min_samples_split=2, n_estimators=600;, score=0.766 total time=   2.5s
[CV 4/5] END max_depth=10, min_samples_leaf=1, min_samples_split=5, n_estimators=700;, score=0.834 total time=   2.5s
[CV 1/5] END max_depth=40, min_samples_leaf=2, min_samples_split=2, n_estimators=600;, score=0.799 total time=   2.6s
[CV 3/5] END max_depth=10, min_samples_leaf=1, min_samples_split=2, n_estimators=600;, score=0.763 total time=   2.1s
[CV 5/5] END max_depth=30, min_samples_leaf=2, min_samples_split=2, n_estimators=600;, score=0.750 total time=   2.7s
[CV 2/5] END max_depth=30, min_samples_leaf=2, min_sam

[CV 2/5] END max_depth=20, min_samples_leaf=2, min_samples_split=2, n_estimators=200;, score=0.761 total time=   0.9s
[CV 3/5] END max_depth=None, min_samples_leaf=2, min_samples_split=2, n_estimators=300;, score=0.768 total time=   1.5s
[CV 3/5] END max_depth=20, min_samples_leaf=2, min_samples_split=5, n_estimators=400;, score=0.766 total time=   1.6s
[CV 5/5] END max_depth=20, min_samples_leaf=1, min_samples_split=2, n_estimators=400;, score=0.781 total time=   2.0s
[CV 2/5] END max_depth=None, min_samples_leaf=1, min_samples_split=5, n_estimators=700;, score=0.794 total time=   4.3s
[CV 3/5] END max_depth=40, min_samples_leaf=2, min_samples_split=5, n_estimators=300;, score=0.768 total time=   1.3s
[CV 5/5] END max_depth=40, min_samples_leaf=2, min_samples_split=2, n_estimators=600;, score=0.775 total time=   2.6s
[CV 5/5] END max_depth=30, min_samples_leaf=1, min_samples_split=5, n_estimators=300;, score=0.758 total time=   1.8s
[CV 2/5] END max_depth=20, min_samples_leaf=2, min_s

[CV 3/5] END max_depth=20, min_samples_leaf=1, min_samples_split=2, n_estimators=400;, score=0.777 total time=   1.8s
[CV 5/5] END max_depth=20, min_samples_leaf=2, min_samples_split=2, n_estimators=600;, score=0.761 total time=   2.5s
[CV 4/5] END max_depth=20, min_samples_leaf=2, min_samples_split=2, n_estimators=200;, score=0.788 total time=   0.9s
[CV 2/5] END max_depth=10, min_samples_leaf=1, min_samples_split=2, n_estimators=200;, score=0.750 total time=   0.9s
[CV 2/5] END max_depth=20, min_samples_leaf=2, min_samples_split=5, n_estimators=700;, score=0.791 total time=   2.9s
[CV 5/5] END max_depth=30, min_samples_leaf=2, min_samples_split=2, n_estimators=600;, score=0.778 total time=   3.0s
[CV 2/5] END max_depth=30, min_samples_leaf=2, min_samples_split=2, n_estimators=400;, score=0.794 total time=   1.7s
[CV 5/5] END max_depth=40, min_samples_leaf=2, min_samples_split=2, n_estimators=700;, score=0.772 total time=   3.3s
[CV 4/5] END max_depth=20, min_samples_leaf=2, min_sampl